In [ ]:
!pip install --upgrade moviepy

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/


In [ ]:
import tensorflow as tf
import PIL
from tensorflow.keras.models import Model
from tensorflow.keras.layers import (Dropout, Dense, Softmax)
from tensorflow.keras.applications import mobilenet as _mobilenet
import random
import os
import numpy as np

In [ ]:
! git clone https://github.com/kenshohara/video-classification-3d-cnn-pytorch.git

Cloning into 'video-classification-3d-cnn-pytorch'...
remote: Enumerating objects: 121, done.
remote: Total 121 (delta 0), reused 0 (delta 0), pack-reused 121
Receiving objects: 100% (121/121), 158.63 KiB | 13.22 MiB/s, done.
Resolving deltas: 100% (63/63), done.


In [ ]:
%cd video-classification-3d-cnn-pytorch/

/content/video-classification-3d-cnn-pytorch/video-classification-3d-cnn-pytorch


In [ ]:
import json
import os
from moviepy.editor import *
from moviepy import *
import shutil

In [ ]:
def loadVideosToInfile(folder):
    videos = os.listdir(folder)
    with open('input', 'w') as inputfile:
      for v in videos:
        if v.split('.')[-1] == 'mp4':
          inputfile.write(v+'\n')


In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [ ]:
# call function to load the filenames to 'input'
loadVideosToInfile('/content/drive/MyDrive/RC11_Skill_Classes/feature')

In [ ]:
# run the model to process all films currently in the input_films folder, and save it to a json file, here named by the date

! python main.py --input input --video_root /content/drive/MyDrive/RC11_Skill_Classes/feature --output /content/drive/MyDrive/RC11_Skill_Classes/0712.json --model /content/drive/MyDrive/resnet-34-kinetics-cpu.pth --mode feature --no_cuda


loading model /content/drive/MyDrive/resnet-34-kinetics-cpu.pth
/content/drive/MyDrive/RC11_Skill_Classes/feature/frame-012713.mp4
ffmpeg version 3.4.11-0ubuntu0.1 Copyright (c) 2000-2022 the FFmpeg developers
  built with gcc 7 (Ubuntu 7.5.0-3ubuntu1~18.04)
  configuration: --prefix=/usr --extra-version=0ubuntu0.1 --toolchain=hardened --libdir=/usr/lib/x86_64-linux-gnu --incdir=/usr/include/x86_64-linux-gnu --enable-gpl --disable-stripping --enable-avresample --enable-avisynth --enable-gnutls --enable-ladspa --enable-libass --enable-libbluray --enable-libbs2b --enable-libcaca --enable-libcdio --enable-libflite --enable-libfontconfig --enable-libfreetype --enable-libfribidi --enable-libgme --enable-libgsm --enable-libmp3lame --enable-libmysofa --enable-libopenjpeg --enable-libopenmpt --enable-libopus --enable-libpulse --enable-librubberband --enable-librsvg --enable-libshine --enable-libsnappy --enable-libsoxr --enable-libspeex --enable-libssh --enable-libtheora --enable-libtwolame --e

In [ ]:
# This function should read all .json files in the output folder, and combine them into one large dictionary.
def readAllOutput(outputFolder):
    dictionaries = {}
    output_files = os.listdir(outputFolder)
    for f in output_files:
      if f.split('.')[-1] == 'json':
        file = open(outputFolder + '/' + f)
        
        segments = json.load(file)
        for s in segments:
          dictionaries[s['video']] = s
       
    return dictionaries

In [ ]:
dicts = readAllOutput('/content/drive/MyDrive/RC11_Skill_Classes/feature')
dicts.keys()

dict_keys(['frame-012713.mp4', 'frame-007860.mp4', 'frame-001343.mp4', 'frame-011012.mp4', 'frame-014618.mp4', 'frame-010140.mp4'])

In [ ]:
dicts['frame-007860.mp4']['clips'][0].keys()

dict_keys(['segment', 'features'])

In [ ]:
# here keyFilmName is the name of the film that you want to find a match for, and the feature dictionary is 
# the dictionary that is given as output by the readAllOutput function

def searchForMatch(keyFilmName, featureDictionary):
    # create variables to keep track of the best clips
    bestRangeStart = 0
    bestRangeFilmName = ''
    bestRangeScore = 1000000000
    
    # first read the features of the keyFilm into keyFeatures
    keyClips = featureDictionary[keyFilmName]['clips']
    keyFeatures = []
    for c in keyClips:
      keyFeatures.append(np.array(c['features']))
    
    # now enter a for loop to go through all films, and see what the best matching sequence is 
    # (we make sure not to check the keyFilm itself by checking it's not that filename)
    for film in featureDictionary.keys():
        if not film == keyFilmName:
          filmClips = featureDictionary[film]['clips']
          filmFeatures = []
          for c in filmClips:
            filmFeatures.append(np.array(c['features']))
          for i in range(len(filmFeatures)-len(keyFeatures)):
            distance = 0
            for j in range(len(keyFeatures)):
              d = np.linalg.norm(filmFeatures[i+j]-keyFeatures[j])
              distance += d
              if distance < bestRangeScore:
                bestRangeScore = distance
                bestRangeStart = i
                bestRangeFilmName = film
                
            
            # so now here 'film' is a filename (which is the key in the feature dictionary of that film)
            # first load the features in a 'filmFeatures' list like we did for key Features
            # then look at the provided code from the lecture to see how to iterate through the other list of features to find the best segment.
            # Now just make sure to also register what film name the best matching segment is from. 
            
    # create a list containing the filename, start and nr of clips
    matchingFragment = [bestRangeFilmName, bestRangeStart, len(keyFeatures)]
    
    return matchingFragment

    # First implement it for the best matching one, then expand it to return the n best matching ones as a list,
    # with n as an argument in the function


In [ ]:
matchingFragment = searchForMatch("frame-007860.mp4", dicts)

In [ ]:
# this is a helper function to which you give the fragment (the output of the searchForMatch function), and it returns
# a moviepy film object (which you can then save)

def extractFragment(fragment, filmFolder):
    # here adapt the code from the lecture, but make it so that it works for any input fragment list
    # the output of the function above: [bestRangeFilmName, bestRangeStart, len(keyFeatures)]
    
    filmFileName = fragment[0]
    start = fragment[1]
    nrClips = fragment[2]
    
    filmPath = os.path.join(filmFolder, filmFileName)
    print(filmPath)
    filmVideo = VideoFileClip(filmPath)
    filmfps = filmVideo.fps
    filmFrameLength = 1/filmfps
    
    nrFrames = nrClips * 16
    startFrame = start * 16
    
    startTime = startFrame * filmFrameLength
    endTime = startTime + nrFrames * filmFrameLength
    
    filmMatchedVideo = filmVideo.subclip(startTime, endTime)
    
    
    return filmMatchedVideo

    # This function should read all .json files in the output folder, and combine them into one large dictionary

In [ ]:
# a small piece of code that moves all processed input films to the processed films folder

input_films_processed = os.listdir('/content/drive/MyDrive/RC11_Skill_Classes/feature')
for file in input_films_processed:
    try:
        shutil.move(os.path.join('/content/drive/MyDrive/RC11_Skill_Classes/feature_processed',file),'/content/drive/MyDrive/RC11_Skill_Classes/feature_processed')
    except:
        print(file + ' not moved')


frame-012713.mp4 not moved
frame-007860.mp4 not moved
frame-001343.mp4 not moved
frame-011012.mp4 not moved
frame-014618.mp4 not moved
frame-010140.mp4 not moved
0712.json not moved
.ipynb_checkpoints not moved


In [ ]:
# read all output with the function declared above

dicts= readAllOutput('/content/drive/MyDrive/RC11_Skill_Classes/feature')

In [ ]:
dicts.keys()

dict_keys(['frame-012713.mp4', 'frame-007860.mp4', 'frame-001343.mp4', 'frame-011012.mp4', 'frame-014618.mp4', 'frame-010140.mp4'])

In [ ]:
fragment = searchForMatch('frame-007860.mp4', dicts)

In [ ]:
fragment

['frame-001343.mp4', 22, 47]

In [ ]:
# extract the fragment from the film
filmFolder = '/content/drive/MyDrive/RC11_Skill_Classes/feature'
fragmentFilm = extractFragment(fragment, filmFolder)

/content/drive/MyDrive/RC11_Skill_Classes/feature/frame-001343.mp4


In [ ]:
# display the film fragment

fragmentFilm.ipython_display()

Moviepy - Building video __temp__.mp4.
MoviePy - Writing audio in __temp__TEMP_MPY_wvf_snd.mp3


MoviePy - Done.
Moviepy - Writing video __temp__.mp4



Moviepy - Done !
Moviepy - video ready __temp__.mp4


In [ ]:
# save the film fragment


fragmentFilm.write_videofile("/content/drive/MyDrive/RC11_Skill_Classes/feature/fragment.mp4", audio_codec='aac')

Moviepy - Building video /content/drive/MyDrive/RC11_Skill_Classes/feature/fragment.mp4.
MoviePy - Writing audio in fragmentTEMP_MPY_wvf_snd.mp4


MoviePy - Done.
Moviepy - Writing video /content/drive/MyDrive/RC11_Skill_Classes/feature/fragment.mp4



Moviepy - Done !
Moviepy - video ready /content/drive/MyDrive/RC11_Skill_Classes/feature/fragment.mp4
